# Início

In [1]:
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import pandas as pd
import copy
from tqdm import tqdm
import time
import os
from scipy import signal
from scipy.signal import find_peaks
from scipy.spatial import distance
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score
from sklearn.decomposition import PCA

In [2]:
files = ['acc_climbingup_forearm.csv',
         'acc_climbingup_thigh.csv',
         'acc_walking_forearm.csv',
         'acc_walking_thigh.csv']
data = pd.read_csv(files[2])

In [3]:
px.line(data.iloc[:,2:])

In [4]:
def picotar(x, J, passo):
    N = x.shape[0]
    Nj = (N-J)//passo + 1
    X = np.zeros((Nj, J))
    for i in range(Nj):
        X[i,:] = x[(i*passo):(i*passo+J)]
    return X

In [5]:
def pcabase(X):
    M = np.ones((X.shape[0],1)).dot(X.mean(axis=0).reshape(1,X.shape[1]))
    R = (X-M).transpose().dot(X-M)
    l, vet = np.linalg.eig(R)
    inds = np.argsort(l)
    vet = vet[:,inds][:,::-1]
    return l, vet

In [6]:
def predlin3d(Xtr):
    X = Xtr[:,:-3]
    y1 = Xtr[:,-1]
    y2 = Xtr[:,-2]
    y3 = Xtr[:,-3]
    pX = np.linalg.inv(X.transpose().dot(X)).dot(X.transpose())
    w1 = pX.dot(y1)
    w2 = pX.dot(y2)
    w3 = pX.dot(y3)
    return w1, w2, w3

In [19]:
s = data.iloc[:,2:].values.reshape(-1)
passo = 3
J = 4*passo
X = picotar(s, J, passo)
w1, w2, w3 = predlin3d(X)
y1h = X[:,:-3].dot(w1)
y2h = X[:,:-3].dot(w2)
y3h = X[:,:-3].dot(w3)

In [24]:
Em = []
passo = 3
for i in tqdm(np.arange(1,150)):
    J = i*passo
    X = picotar(s, J, passo)
    w1, w2, w3 = predlin3d(X)
    y1h = X[:,:-3].dot(w1)
    y2h = X[:,:-3].dot(w2)
    y3h = X[:,:-3].dot(w3)
    erro = X[:,-3:] - np.vstack((y3h, y2h, y1h)).transpose()
    Em.append(np.sqrt(np.sum(erro**2, axis=1)).mean())

In [26]:
px.scatter(Em)

In [25]:
print('Investigar o atraso de uma amostra nos valores estimados!')
fig = go.Figure()
fig.add_trace(go.Scatter(y=X[:,-1], mode='lines', showlegend=True, name='1original'))
fig.add_trace(go.Scatter(y=y1h, mode='lines', showlegend=True, name='1predição'))
fig.add_trace(go.Scatter(y=X[:,-2], mode='lines', showlegend=True, name='2original'))
fig.add_trace(go.Scatter(y=y2h, mode='lines', showlegend=True, name='2predição'))
fig.add_trace(go.Scatter(y=X[:,-3], mode='lines', showlegend=True, name='3original'))
fig.add_trace(go.Scatter(y=y3h, mode='lines', showlegend=True, name='3predição'))

Investigar o atraso de uma amostra nos valores estimados!


# Pegando os dados

In [41]:
pasta = 'C:\\Meu Drive\\Doutorado Unicamp\\Projeto\\Dataset\\realworldcsvs\\proband1\\acc\\'
vals = []
for file in os.listdir(pasta):
    data = pd.read_csv(pasta+file)
    vals.append(len(data))

In [61]:
fig = px.scatter(np.array(vals))
fig.update_layout(
    xaxis = dict(
        tickvals = np.arange(56),
        ticktext = os.listdir(pasta)
    )
)

In [45]:
# Vamos remover a atividade 'jumping'
actis = ['climbingdown', 'climbingup', 'lying', 'running', 'sitting', 'standing', 'walking']
posis = ['chest', 'forearm', 'head', 'shin', 'thigh', 'upperarm', 'waist']
users = ['proband' + x for x in np.arange(1,16).astype(str)]

In [62]:
# proband2 não tem acc_climbingup_forearm
users.remove('proband2')
# # proband4 não tem acc_walking_chest
# users.remove('proband4')
# # proband6 não tem acc_sitting_chest
# users.remove('proband6')

In [63]:
users

['proband1',
 'proband3',
 'proband4',
 'proband5',
 'proband6',
 'proband7',
 'proband8',
 'proband9',
 'proband10',
 'proband11',
 'proband12',
 'proband13',
 'proband14',
 'proband15']

In [47]:
pasta = 'C:\\Meu Drive\\Doutorado Unicamp\\Projeto\\Dataset\\realworldcsvs\\'
vals = []
for user in users:
    for sen in ['acc', 'gyr']:
        for file in os.listdir(pasta+user+'\\'+sen):
            data = pd.read_csv(pasta+user+'\\'+sen+'\\'+file)
            vals.append(len(data))

In [48]:
px.scatter(vals)

In [64]:
pasta = 'C:\\Meu Drive\\Doutorado Unicamp\\Projeto\\Dataset\\realworldcsvs\\'
dadosAcc = []
dadosGyr = []
rotulos = []
for user in tqdm(users):
    for pos in posis:
        acc = []
        gyr = []
        sub = []
        for act in actis:
            files = os.listdir(pasta+user+'\\acc\\')
            ind = [(file.find(act)>-1) and (file.find(pos)>-1) for file in files].index(True)
            acc.append(pd.read_csv(pasta+user+'\\acc\\'+files[ind]))
            files = os.listdir(pasta+user+'\\gyr\\')
            ind = [(file.find(act)>-1) and (file.find(pos)>-1) for file in files].index(True)
            gyr.append(pd.read_csv(pasta+user+'\\gyr\\'+files[ind]))
            sub.append(pos+act)
        dadosAcc.append(acc)
        dadosGyr.append(gyr)
        rotulos.append(sub)